In [1]:
%pip install ultralytics

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 59.3 MB/s eta 0:00:00


In [2]:
from google.colab import files
uploaded = files.upload()

Saving best (2).pt to best (2).pt


In [3]:
from google.colab import files
uploaded = files.upload()

Saving sample_video.mp4 to sample_video.mp4


In [4]:
import base64
from IPython.display import HTML, display

def show_mp4(path, width=640):
    """
    Reads an MP4 from disk and embeds it as an HTML5 video in Colab.

    Args:
        path (str): path to the .mp4 file
        width (int): display width in pixels
    """
    # Read & encode
    with open(path, 'rb') as f:
        mp4_bytes = f.read()
    b64 = base64.b64encode(mp4_bytes).decode()

    # Build HTML
    html = f'''
    <video width="{width}" controls autoplay loop muted playsinline>
        <source src="data:video/mp4;base64,{b64}" type="video/mp4">
        Your browser does not support HTML5 video.
    </video>
    '''
    display(HTML(html))


In [5]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [6]:
show_mp4('/content/sample_video.mp4')

In [7]:
from ultralytics import YOLO

model = YOLO("/content/best.pt")


def bytetrack(path):
    results = model.track(
        source=path,
        tracker="bytetrack.yaml",
        persist=True,
        stream=True,
    )


    for frame_id, result in enumerate(results):

        if result.boxes is not None and result.boxes.id is not None:
            track_ids = result.boxes.id.int().cpu().tolist()
            bboxes = result.boxes.xyxy.cpu().tolist()
            confidences = result.boxes.conf.cpu().tolist()
            class_ids = result.boxes.cls.int().cpu().tolist()


            for track_id, bbox, conf, cls_id in zip(track_ids, bboxes, confidences, class_ids):
                print(
                    f"Frame {frame_id}: "
                    f"Track ID {track_id}, Class {cls_id}, "
                    f"Confidence {conf:.2f}, BBox {bbox}"
                )




Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


In [8]:
import cv2
import random
import os
import json
from ultralytics import YOLO


model = YOLO("/content/best.pt")

def bytetrack(path, output_path, json_path, target_classes=None):
    """
    Performs object tracking on a video file using YOLOv8 and ByteTrack.
    Saves both an annotated video and a JSON file with tracking results.
    """

    output_dir = os.path.dirname(output_path)
    if output_dir:
        os.makedirs(output_dir, exist_ok=True)
        print(f"Ensured output directory exists: {output_dir}")


    cap = cv2.VideoCapture(path)
    if not cap.isOpened():
        print("Error opening video file")
        return


    fps = cap.get(cv2.CAP_PROP_FPS)
    width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
    height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))


    fourcc = cv2.VideoWriter_fourcc(*"mp4v")
    out = cv2.VideoWriter(output_path, fourcc, fps, (width, height))


    track_id_colors = {}


    output_data = []


    results = model.track(
        source=path,
        tracker="bytetrack.yaml",
        persist=True,
        stream=True,
        classes=target_classes
    )

    print("Processing video frames. Please wait...")
    for frame_id, result in enumerate(results):
        frame = result.orig_img.copy()

        if result.boxes is not None and result.boxes.id is not None:
            track_ids = result.boxes.id.int().cpu().tolist()
            bboxes = result.boxes.xyxy.cpu().tolist()
            class_ids = result.boxes.cls.int().cpu().tolist()

            for track_id, bbox, cls_id in zip(track_ids, bboxes, class_ids):
                if target_classes and cls_id not in target_classes:
                    continue


                if track_id not in track_id_colors:
                    track_id_colors[track_id] = (
                        random.randint(0, 255),
                        random.randint(0, 255),
                        random.randint(0, 255)
                    )
                color = track_id_colors[track_id]


                x1, y1, x2, y2 = map(int, bbox)


                cv2.rectangle(frame, (x1, y1), (x2, y2), color, 3)


                text = f"ID: {track_id}"
                cv2.putText(frame, text, (x1, max(0, y1 - 10)),
                            cv2.FONT_HERSHEY_SIMPLEX, 1.0, color, 2)


                output_data.append({
                    "frame": frame_id,
                    "id": track_id,
                    "class_id": cls_id,
                    "bbox": [x1, y1, x2, y2]
                })


        out.write(frame)
        print(f"Processed frame {frame_id}", end='\r')


    out.release()

    with open(json_path, "w") as f:
        json.dump(output_data, f, indent=4)

    print("\n\nVideo processing complete!")
    print(f"✅ Saved video: {output_path}")
    print(f"✅ Saved JSON: {json_path}")


In [10]:
bytetrack(
    "/content/sample_video.mp4",
    "/content/drive/MyDrive/result/result-3.mp4",
    "/content/drive/MyDrive/result/result-2.json",
    target_classes=[0,1,2,3,4,5,6]
)

Ensured output directory exists: /content/drive/MyDrive/result
requirements: Ultralytics requirement ['lap>=0.5.12'] not found, attempting AutoUpdate...

requirements: AutoUpdate success ✅ 0.7s
WARNING ⚠️ requirements: Restart runtime or rerun command for updates to take effect

Processing video frames. Please wait...

video 1/1 (frame 1/349) /content/sample_video.mp4: 384x640 1 Human, 1 Bus, 47.7ms
video 1/1 (frame 2/349) /content/sample_video.mp4: 384x640 1 Human, 1 Bus, 9.4ms
video 1/1 (frame 3/349) /content/sample_video.mp4: 384x640 1 Human, 1 Bus, 8.4ms
video 1/1 (frame 4/349) /content/sample_video.mp4: 384x640 1 Human, 1 Bus, 9.2ms
video 1/1 (frame 5/349) /content/sample_video.mp4: 384x640 1 Human, 1 Bus, 8.2ms
video 1/1 (frame 6/349) /content/sample_video.mp4: 384x640 2 Humans, 1 Bus, 7.8ms
video 1/1 (frame 7/349) /content/sample_video.mp4: 384x640 4 Humans, 1 Bus, 10.7ms
video 1/1 (frame 8/349) /content/sample_video.mp4: 384x640 5 Humans, 1 Bus, 8.9ms
video 1/1 (frame 9/349) /c